In [6]:
import geopandas as gpd
import plotly.express as px
import json
import os

# Define shapefile paths with double backslashes
shapefile_paths = {
    "CON22": "C:\\Users\\xrcru\\OneDrive\\Documents\\Spring25\\GeoComp1\\Lab_06\\Data\\CON22\\CON22_June_03_2022\\CON22_June_03_2022.shp",
    "SEN22": "C:\\Users\\xrcru\\OneDrive\\Documents\\Spring25\\GeoComp1\\Lab_06\\Data\\SEN22\\SEN22_June_03_2022\\SEN22_June_03_2022.shp", 
    "ASSEMBLY22": "C:\\Users\\xrcru\\OneDrive\\Documents\\Spring25\\GeoComp1\\Lab_06\\Data\\2022Assembly\\2022assembly_shape_file\\Assembly22.shp"
}

# Load existing shapefiles into GeoDataFrames
gdfs = {key: gpd.read_file(path) for key, path in shapefile_paths.items() if os.path.exists(path)}

if not gdfs:
    print("❌ No valid shapefiles found. Exiting...")
    exit()

# Convert all GeoDataFrames to latitude/longitude (EPSG:4326)
gdfs = {key: gdf.to_crs(epsg=4326) if gdf.crs else gdf for key, gdf in gdfs.items()}

# Export all datasets into a single GeoPackage
geopackage_path = "C:\\Users\\xrcru\\OneDrive\\Documents\\Spring25\\GeoComp1\\Lab_06\\output_data.gpkg"
for i, (key, gdf) in enumerate(gdfs.items()):
    gdf.to_file(geopackage_path, layer=key, driver="GPKG", mode="w" if i == 0 else "a")

print(f"✅ Exported all layers into: {geopackage_path}")

# Visualize the first dataset using Plotly
key, gdf = next(iter(gdfs.items()))
print(f"🔍 Previewing map for {key}...")

# Select a numeric column for color mapping
color_column = next((col for col in gdf.select_dtypes("number").columns), None)
if color_column is None:
    gdf["dummy_value"] = range(len(gdf))
    color_column = "dummy_value"

# Convert geometry to GeoJSON
geojson_data = json.loads(gdf.to_json())

# Create and display the map
fig = px.choropleth(
    gdf,
    geojson=geojson_data,
    locations=gdf.index,
    color=color_column,
    title=f"Map of {key}",
    projection="mercator"
)
fig.update_geos(fitbounds="locations", visible=False)
fig.show()


✅ Exported all layers into: C:\Users\xrcru\OneDrive\Documents\Spring25\GeoComp1\Lab_06\output_data.gpkg
🔍 Previewing map for CON22...
